In [1]:
import numpy as np
import pandas as pd
from pandas.tseries.offsets import Hour, Minute
from pandas.tseries.offsets import Day, MonthEnd
from pandas.tseries.offsets import Hour
from sklearn.model_selection import TimeSeriesSplit
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_squared_error as mse
from keras.preprocessing.sequence import TimeseriesGenerator
import xgboost as xgb

np.random.seed(42)


In [2]:

global busses
busses = ['309_WIND_1', '317_WIND_1', '303_WIND_1', '122_WIND_1']
df = pd.read_csv('Wind_deseason_15.csv', parse_dates=[0], index_col=0)



In [3]:
def lags(df, n):
    
    df_new = df
    
    for i in range(n):
        name = "lag "+ str(i+1)
        df_new[name] = df['309_WIND_1'].shift(i+1)
    
    return df_new
    

In [4]:
def TrainTest(df):
    
    num_rows = df.shape[0]
    
    num_training = (num_rows * 8)//10
   
    #train = df.iloc[0:num_training]
    #test = df.iloc[num_training:num_rows]
    
    
    return num_training 

In [5]:
def TestModel(X,test, mod):
    
    MSEs = []
    
    for i in range(len(X)):
        
        print(X.iloc[i].to_frame().transpose())
        pred = mod.predict(X.iloc[i].to_frame().transpose())
        #pred = scaler.inverse_transform(pred)
        
        print(pred)
        print(test.iloc[i])
        
        MSEs.append(mse([test.iloc[i]],pred))
        
        
    return MSEs

In [6]:
def model1Train(X_train,Y_train,X_test,Y_test):
    mod = xgb.XGBRegressor()
    mod.fit(X_train, Y_train, eval_set = [(X_train, Y_train),(X_test, Y_test)])#keep low for now, edit later eval_set = [(X_train, y_train),(X_test, y_test)]
    
    return mod


In [7]:
def model2Train(X_train,Y_train):
    mod = xgb.XGBRegressor()
    mod.fit(X_train, Y_train)#keep low for now, edit later eval_set = [(X_train, y_train),(X_test, y_test)]
    
    return mod

In [8]:
def runModels(df, last):
    scaler = MinMaxScaler()
     
    bound = TrainTest(df)
    
    
    last_index =pd.DatetimeIndex(data = [idx.replace(year = 2019) for idx in last.index])
    df_index = df.index
    new_df_idx = last_index.append(df_index)
    
    array_df = df['309_WIND_1'].to_numpy()
    
    array_df = np.append(last['309_WIND_1'].to_numpy(), array_df)
    
    
    
    new_df = pd.DataFrame(array_df, columns = ['309_WIND_1'])
    new_df['Dates'] = new_df_idx
    new_df = new_df.set_index('Dates')
    

    
    
    lag = lags(new_df, 107)
    
    lag = lag[lag.columns[::-1]]
    

    
    
    lagged_train = lag.iloc[107:bound+107]
    lagged_test = lag.iloc[bound+107:]

    X_train = lagged_train.drop('309_WIND_1', axis = 1)
    Y_train = lagged_train['309_WIND_1']
    
    X_test = lagged_test.drop('309_WIND_1', axis = 1)
    Y_test = lagged_test['309_WIND_1']
    
    print(X_train)
    print(X_test)
  
    
    #mod = model1Train(X_train, Y_train,X_test, Y_test)
    mod = model2Train(X_train, Y_train)
    
    Tests = TestModel(X_test, Y_test, mod)
    
    print(Tests)
    
    return Tests

    
    

In [9]:

df1 = df[df.index.month.isin([1,2,3])]
df2 = df[df.index.month.isin([4,5,6])]
df3 = df[df.index.month.isin([7,8,9])]
df4 = df[df.index.month.isin([10,11,12])]

In [10]:
mse1 = runModels(df1,df4.iloc[-107:])

C:\Users\bvits\AppData\Local\Temp\ipykernel_41448\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_41448\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_41448\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider

                       lag 107    lag 106    lag 105    lag 104    lag 103  \
Dates                                                                        
2020-01-01 00:15:00  40.448957  34.680895  17.846166  32.878104  59.010041   
2020-01-01 00:30:00  34.680895  17.846166  32.878104  59.010041  43.241979   
2020-01-01 00:45:00  17.846166  32.878104  59.010041  43.241979  28.607250   
2020-01-01 01:00:00  32.878104  59.010041  43.241979  28.607250  -0.694145   
2020-01-01 01:15:00  59.010041  43.241979  28.607250  -0.694145 -18.362208   
...                        ...        ...        ...        ...        ...   
2020-03-13 18:00:00  90.941599  94.979552  93.750838  94.255458  90.360077   
2020-03-13 18:15:00  94.979552  93.750838  94.255458  90.360077  82.598030   
2020-03-13 18:30:00  93.750838  94.255458  90.360077  82.598030  78.769316   
2020-03-13 18:45:00  94.255458  90.360077  82.598030  78.769316  72.473935   
2020-03-13 19:00:00  90.360077  82.598030  78.769316  72.473935 

                      lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-03-13 19:15:00  82.59803  78.769316  72.473935  76.778555  71.549841   

                      lag 102   lag 101    lag 100     lag 99     lag 98  ...  \
2020-03-13 19:15:00  74.15446  81.05908  83.330366  69.934985  61.239605  ...   

                        lag 10      lag 9      lag 8      lag 7      lag 6  \
2020-03-13 19:15:00 -24.198086 -22.660134 -22.388847 -24.217561 -27.612942   

                         lag 5     lag 4      lag 3      lag 2      lag 1  
2020-03-13 19:15:00 -30.841656 -30.97037 -30.632417 -33.527797 -34.789845  

[1 rows x 107 columns]
[-35.35949]
-35.25189187235375
                       lag 107    lag 106    lag 105    lag 104   lag 103  \
2020-03-13 19:30:00  78.769316  72.473935  76.778555  71.549841  74.15446   

                      lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-03-13 19:30:00  81.05908  83.330366  69.934985  61.239605  71.777558   

        

[-37.4861]
-38.153886205142925
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-03-13 23:00:00  63.233988  55.871941  56.809894  29.547847  67.052466   

                       lag 102    lag 101    lag 100     lag 99    lag 98  \
2020-03-13 23:00:00  58.890419  33.895038  35.299658  43.370944  45.84223   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-03-13 23:00:00  ... -38.462128 -38.724175 -38.419556 -38.414936   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-03-13 23:00:00 -38.576983 -38.772364 -38.401078 -38.429792 -38.558506   

                         lag 1  
2020-03-13 23:00:00 -38.153886  

[1 rows x 107 columns]
[-34.63456]
-38.38260008605644
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-03-13 23:15:00  55.871941  56.809894  29.547847  67.052466  58.890419   

                       lag 102    lag 101    lag 100    lag 99     lag 98  \


[-35.70284]
-38.42589141411064
                       lag 107   lag 106    lag 105    lag 104    lag 103  \
2020-03-14 02:45:00  43.659077  51.19703  55.968316  50.439602  26.844221   

                       lag 102   lag 101   lag 100     lag 99     lag 98  ...  \
2020-03-14 02:45:00  10.382174 -0.179873  2.224746  15.596033  23.100652  ...   

                      lag 10      lag 9      lag 8      lag 7      lag 6  \
2020-03-14 02:45:00 -48.0008 -48.829514 -48.124894 -48.120275 -47.982322   

                         lag 5      lag 4      lag 3      lag 2      lag 1  
2020-03-14 02:45:00 -46.711036 -45.606416 -42.701797 -39.130511 -38.425891  

[1 rows x 107 columns]
[-36.959507]
-36.52127196169083
                      lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-03-14 03:00:00  51.19703  55.968316  50.439602  26.844221  10.382174   

                      lag 102   lag 101    lag 100     lag 99     lag 98  ...  \
2020-03-14 03:00:00 -0.179873  2.224746  15.596033  

...

[-14.328357]
-12.029971645485997
                       lag 107    lag 106    lag 105   lag 104   lag 103  \
2020-03-31 04:30:00 -24.033652 -19.929098 -27.424544 -30.01999 -29.54877   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-03-31 04:30:00 -31.377549 -34.472995 -32.901775 -25.330554 -20.092667   

                     ...    lag 10      lag 9      lag 8      lag 7  \
2020-03-31 04:30:00  ... -9.237624 -12.366404 -26.828516 -24.890629   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-03-31 04:30:00 -23.719408 -14.681521 -22.676967 -24.905746 -16.067859   

                         lag 1  
2020-03-31 04:30:00 -12.029972  

[1 rows x 107 columns]
[-14.529223]
-17.725417661202712
                       lag 107    lag 106   lag 105   lag 104    lag 103  \
2020-03-31 04:45:00 -19.929098 -27.424544 -30.01999 -29.54877 -31.377549   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
202

[-13.742413]
-15.790441230286758
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-03-31 08:30:00 -36.960789 -38.956235 -39.318347 -39.047127 -39.042573   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-03-31 08:30:00 -39.338019 -39.366798 -39.162244 -39.391023 -39.119803   

                     ...   lag 10    lag 9      lag 8      lag 7      lag 6  \
2020-03-31 08:30:00  ... -7.06476 -9.99354 -11.722319 -14.884432 -17.813211   

                         lag 5     lag 4      lag 3      lag 2      lag 1  
2020-03-31 08:30:00 -14.508657 -11.67077 -13.632883 -12.994995 -15.790441  

[1 rows x 107 columns]
[-15.059081]
-6.652553912670145
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-03-31 08:45:00 -38.956235 -39.318347 -39.047127 -39.042573 -39.338019   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-03-31 08:45:00 -39.366798 -39.162244 -39.39102

[-31.651852]
-33.15091081508752
                       lag 107    lag 106    lag 105   lag 104    lag 103  \
2020-03-31 12:30:00 -38.921258 -39.116704 -39.645484 -39.14093 -38.669709   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-03-31 12:30:00 -38.998488 -39.193934 -39.256047 -38.951493 -39.180272   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-03-31 12:30:00  ... -24.591897 -22.920676 -25.416122 -27.978235   

                         lag 6     lag 5      lag 4      lag 3      lag 2  \
2020-03-31 12:30:00 -28.273681 -30.70246 -28.764573 -28.993352 -31.455465   

                         lag 1  
2020-03-31 12:30:00 -33.150911  

[1 rows x 107 columns]
[-32.632504]
-30.179690164137572
                       lag 107    lag 106   lag 105    lag 104    lag 103  \
2020-03-31 12:45:00 -39.116704 -39.645484 -39.14093 -38.669709 -38.998488   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \


[-31.636179]
-33.37349308227167
                       lag 107   lag 106    lag 105    lag 104    lag 103  \
2020-03-31 16:45:00 -38.210507 -37.47262 -37.501399 -39.063512 -37.725625   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-03-31 16:45:00 -37.754404 -37.216517 -37.845296 -38.874075 -37.802855   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-03-31 16:45:00  ... -27.181146 -28.743258 -32.238704 -31.900817   

                        lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-03-31 16:45:00 -28.46293 -30.325042 -27.453822 -29.649268 -31.244714   

                         lag 1  
2020-03-31 16:45:00 -33.373493  

[1 rows x 107 columns]
[-35.824455]
-32.86893909798838
                      lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-03-31 17:00:00 -37.47262 -37.501399 -39.063512 -37.725625 -37.754404   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2

[-34.57963]
-33.458188031839185
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-03-31 21:15:00 -34.495202 -36.623981 -37.119428 -35.014874 -32.743653   

                       lag 102    lag 101    lag 100     lag 99    lag 98  \
2020-03-31 21:15:00 -30.905766 -28.034545 -25.563324 -19.692104 -15.18755   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-03-31 21:15:00  ...  29.067493 -16.961287 -27.090066 -18.852179   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-03-31 21:15:00 -21.147625 -29.976404 -33.338517 -33.533963 -33.829409   

                         lag 1  
2020-03-31 21:15:00 -33.458188  

[1 rows x 107 columns]
[-33.92676]
-33.153634047555904
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-03-31 21:30:00 -36.623981 -37.119428 -35.014874 -32.743653 -30.905766   

                       lag 102    lag 101    lag 100    lag 99     lag 98  

In [11]:
mse2 = runModels(df2,df1.iloc[-107:])

C:\Users\bvits\AppData\Local\Temp\ipykernel_41448\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_41448\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_41448\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider

                        lag 107     lag 106     lag 105     lag 104  \
Dates                                                                 
2020-04-01 00:00:00  -26.473888  -25.536000  -20.331446  -19.326892   
2020-04-01 00:15:00  -25.536000  -20.331446  -19.326892  -18.455672   
2020-04-01 00:30:00  -20.331446  -19.326892  -18.455672  -19.117784   
2020-04-01 00:45:00  -19.326892  -18.455672  -19.117784  -23.179897   
2020-04-01 01:00:00  -18.455672  -19.117784  -23.179897  -24.875343   
...                         ...         ...         ...         ...   
2020-06-12 17:45:00  100.220067  107.687854  109.888974  116.456761   
2020-06-12 18:00:00  107.687854  109.888974  116.456761  121.091214   
2020-06-12 18:15:00  109.888974  116.456761  121.091214  123.092334   
2020-06-12 18:30:00  116.456761  121.091214  123.092334  126.993454   
2020-06-12 18:45:00  121.091214  123.092334  126.993454  127.061241   

                        lag 103     lag 102     lag 101     lag 100  \
Dates

                        lag 107     lag 106     lag 105     lag 104  \
2020-06-12 19:00:00  123.092334  126.993454  127.061241  128.529028   

                        lag 103     lag 102     lag 101     lag 100  \
2020-06-12 19:00:00  127.330148  128.664601  128.365721  127.966841   

                         lag 99      lag 98  ...     lag 10      lag 9  \
2020-06-12 19:00:00  127.701295  128.002415  ... -21.405391 -21.270938   

                         lag 8      lag 7      lag 6      lag 5      lag 4  \
2020-06-12 19:00:00 -21.269818 -21.702031 -21.200911 -20.499791 -18.332004   

                         lag 3      lag 2      lag 1  
2020-06-12 19:00:00 -18.497551 -18.963097 -20.461977  

[1 rows x 107 columns]
[-19.859005]
-20.89419052438829
                        lag 107     lag 106     lag 105     lag 104  \
2020-06-12 19:15:00  126.993454  127.061241  128.529028  127.330148   

                        lag 103     lag 102     lag 101     lag 100  \
2020-06-12 19:15:00  128.664

[-19.855469]
-17.044056103353654
                       lag 107    lag 106    lag 105    lag 104   lag 103  \
2020-06-12 23:00:00  44.743589  30.311376  21.712496  19.880282  7.181402   

                      lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-12 23:00:00 -5.884144 -12.349691 -16.381904 -17.414117 -17.146331   

                     ...     lag 10      lag 9     lag 8      lag 7     lag 6  \
2020-06-12 23:00:00  ... -21.254137 -21.019683 -20.68523 -21.717443 -21.48299   

                        lag 5      lag 4      lag 3      lag 2      lag 1  
2020-06-12 23:00:00 -21.28187 -21.314083 -21.212963 -21.011843 -17.044056  

[1 rows x 107 columns]
[-16.712193]
-14.2096026975069
                       lag 107    lag 106    lag 105   lag 104   lag 103  \
2020-06-12 23:15:00  30.311376  21.712496  19.880282  7.181402 -5.884144   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-12 23:15:00 -12.349691 -16.381904 -17.414117 -17

[-12.691484]
-12.369217994020364
                      lag 107   lag 106   lag 105   lag 104    lag 103  \
2020-06-13 03:15:00 -5.877076  1.890711  4.525164  8.859618  15.960738   

                       lag 102    lag 101    lag 100     lag 99    lag 98  \
2020-06-13 03:15:00  23.861858  26.729645  18.997431  16.265218  7.199671   

                     ...    lag 10     lag 9     lag 8     lag 7      lag 6  \
2020-06-13 03:15:00  ... -7.479299 -7.144845 -8.043725 -8.609272 -11.141485   

                         lag 5      lag 4      lag 3      lag 2      lag 1  
2020-06-13 03:15:00 -11.473698 -12.272578 -12.204791 -12.170338 -12.369218  

[1 rows x 107 columns]
[-12.542552]
-12.13476458817361
                      lag 107   lag 106   lag 105    lag 104    lag 103  \
2020-06-13 03:30:00  1.890711  4.525164  8.859618  15.960738  23.861858   

                       lag 102    lag 101    lag 100    lag 99    lag 98  ...  \
2020-06-13 03:30:00  26.729645  18.997431  16.265218  7.199671

...

[0.9454125]
-1.1800143521049948
                       lag 107   lag 106    lag 105    lag 104   lag 103  \
2020-06-30 03:45:00 -15.024734 -14.15744 -14.856814 -11.789521 -6.255561   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-30 03:45:00 -4.954934  2.945693  1.046319  5.246946  4.780906  ...   

                        lag 10      lag 9     lag 8     lag 7     lag 6  \
2020-06-30 03:45:00 -15.585654 -15.085028 -8.517734 -1.650441 -1.649814   

                        lag 5     lag 4     lag 3     lag 2     lag 1  
2020-06-30 03:45:00 -2.182521  1.684772 -2.014601 -0.147308 -1.180014  

[1 rows x 107 columns]
[-0.13531694]
8.353945630148722
                      lag 107    lag 106    lag 105   lag 104   lag 103  \
2020-06-30 04:00:00 -14.15744 -14.856814 -11.789521 -6.255561 -4.954934   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-30 04:00:00  2.945693  1.046319  5.246946  4.780906  5.214866  ...   


[-15.00347]
-15.40206800487141
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-30 08:15:00 -2.546787 -0.612827 -3.878867  1.021759  0.155719   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-30 08:15:00  3.823012  1.490306 -7.209068 -8.075108 -9.274481  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-06-30 08:15:00  8.192292  7.959585  2.426879  1.094172 -1.738535   

                         lag 5     lag 4      lag 3      lag 2      lag 1  
2020-06-30 08:15:00 -10.371241 -7.137281 -12.203321 -15.602695 -15.402068  

[1 rows x 107 columns]
[-14.99413]
-17.034774689284358
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-30 08:30:00 -0.612827 -3.878867  1.021759  0.155719  3.823012   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-30 08:30:00  1.490306 -7.209068 -8.075108 -9.274481 -9.607188  ...   

      

[-20.728743]
-18.924748306558204
                      lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 12:30:00 -9.636134 -11.135508 -14.168214 -13.600921 -13.466961   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 12:30:00 -16.233001 -16.232375 -16.665081 -16.564455 -17.363828   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-06-30 12:30:00  ... -18.930388 -18.663095 -19.162468 -18.728508   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-06-30 12:30:00 -18.994548 -18.893922 -18.826628 -18.859335 -18.892042   

                         lag 1  
2020-06-30 12:30:00 -18.924748  

[1 rows x 107 columns]
[-18.500965]
-19.05745499097116
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 12:45:00 -11.135508 -14.168214 -13.600921 -13.466961 -16.233001   

                       lag 102    lag 101    lag 100     lag 99     lag 98

[-14.905429]
-14.580761941578334
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 16:45:00 -18.558815 -18.658188 -18.390895 -18.590268 -18.389641   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 16:45:00 -18.322348 -18.288388 -18.687762 -18.253802 -18.519842   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-06-30 16:45:00  ... -18.586402 -17.919108 -17.851815 -17.451189   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-06-30 16:45:00 -16.983895 -16.983269 -15.849309 -15.682015 -15.248055   

                         lag 1  
2020-06-30 16:45:00 -14.580762  

[1 rows x 107 columns]
[-14.045472]
-14.413468625991284
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 17:00:00 -18.658188 -18.390895 -18.590268 -18.389641 -18.322348   

                       lag 102    lag 101    lag 100     lag 99     lag

[-8.427326]
-6.804068892185518
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 20:45:00 -18.448788 -18.181495 -18.214202 -18.280242 -17.579615   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 20:45:00 -18.012322 -17.311695 -17.577735 -18.110442 -17.876482   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-06-30 20:45:00  ... -11.143042 -10.342415 -10.541789 -10.041162   

                        lag 6     lag 5     lag 4     lag 3     lag 2  \
2020-06-30 20:45:00 -8.907202 -8.773242 -8.339282 -7.571989 -7.471362   

                        lag 1  
2020-06-30 20:45:00 -6.804069  

[1 rows x 107 columns]
[-8.106596]
-6.003442243265133
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 21:00:00 -18.181495 -18.214202 -18.280242 -17.579615 -18.012322   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-3

In [12]:
mse3 = runModels(df2,df.iloc[-107:])

C:\Users\bvits\AppData\Local\Temp\ipykernel_41448\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_41448\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_41448\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider

                        lag 107     lag 106     lag 105     lag 104  \
Dates                                                                 
2020-04-01 00:00:00   34.680895   17.846166   32.878104   59.010041   
2020-04-01 00:15:00   17.846166   32.878104   59.010041   43.241979   
2020-04-01 00:30:00   32.878104   59.010041   43.241979   28.607250   
2020-04-01 00:45:00   59.010041   43.241979   28.607250   -0.694145   
2020-04-01 01:00:00   43.241979   28.607250   -0.694145  -18.362208   
...                         ...         ...         ...         ...   
2020-06-12 17:45:00  100.220067  107.687854  109.888974  116.456761   
2020-06-12 18:00:00  107.687854  109.888974  116.456761  121.091214   
2020-06-12 18:15:00  109.888974  116.456761  121.091214  123.092334   
2020-06-12 18:30:00  116.456761  121.091214  123.092334  126.993454   
2020-06-12 18:45:00  121.091214  123.092334  126.993454  127.061241   

                        lag 103     lag 102     lag 101     lag 100  \
Dates

                        lag 107     lag 106     lag 105     lag 104  \
2020-06-12 19:00:00  123.092334  126.993454  127.061241  128.529028   

                        lag 103     lag 102     lag 101     lag 100  \
2020-06-12 19:00:00  127.330148  128.664601  128.365721  127.966841   

                         lag 99      lag 98  ...     lag 10      lag 9  \
2020-06-12 19:00:00  127.701295  128.002415  ... -21.405391 -21.270938   

                         lag 8      lag 7      lag 6      lag 5      lag 4  \
2020-06-12 19:00:00 -21.269818 -21.702031 -21.200911 -20.499791 -18.332004   

                         lag 3      lag 2      lag 1  
2020-06-12 19:00:00 -18.497551 -18.963097 -20.461977  

[1 rows x 107 columns]
[-19.995272]
-20.89419052438829
                        lag 107     lag 106     lag 105     lag 104  \
2020-06-12 19:15:00  126.993454  127.061241  128.529028  127.330148   

                        lag 103     lag 102     lag 101     lag 100  \
2020-06-12 19:15:00  128.664

[-16.78829]
-14.2096026975069
                       lag 107    lag 106    lag 105   lag 104   lag 103  \
2020-06-12 23:15:00  30.311376  21.712496  19.880282  7.181402 -5.884144   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-12 23:15:00 -12.349691 -16.381904 -17.414117 -17.146331 -17.178544   

                     ...     lag 10     lag 9      lag 8     lag 7     lag 6  \
2020-06-12 23:15:00  ... -21.019683 -20.68523 -21.717443 -21.48299 -21.28187   

                         lag 5      lag 4      lag 3      lag 2      lag 1  
2020-06-12 23:15:00 -21.314083 -21.212963 -21.011843 -17.044056 -14.209603  

[1 rows x 107 columns]
[-15.131156]
-16.408482624993482
                       lag 107    lag 106   lag 105   lag 104    lag 103  \
2020-06-12 23:30:00  21.712496  19.880282  7.181402 -5.884144 -12.349691   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-12 23:30:00 -16.381904 -17.414117 -17.146331 -17.

[-12.818177]
-12.13476458817361
                      lag 107   lag 106   lag 105    lag 104    lag 103  \
2020-06-13 03:30:00  1.890711  4.525164  8.859618  15.960738  23.861858   

                       lag 102    lag 101    lag 100    lag 99    lag 98  ...  \
2020-06-13 03:30:00  26.729645  18.997431  16.265218  7.199671  3.900792  ...   

                       lag 10     lag 9     lag 8      lag 7      lag 6  \
2020-06-13 03:30:00 -7.144845 -8.043725 -8.609272 -11.141485 -11.473698   

                         lag 5      lag 4      lag 3      lag 2      lag 1  
2020-06-13 03:30:00 -12.272578 -12.204791 -12.170338 -12.369218 -12.134765  

[1 rows x 107 columns]
[-11.513988]
-12.36697784899352
                      lag 107   lag 106    lag 105    lag 104    lag 103  \
2020-06-13 03:45:00  4.525164  8.859618  15.960738  23.861858  26.729645   

                       lag 102    lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-13 03:45:00  18.997431  16.265218  7.199671  3.90079

...

[-15.113252]
-15.40206800487141
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-30 08:15:00 -2.546787 -0.612827 -3.878867  1.021759  0.155719   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-30 08:15:00  3.823012  1.490306 -7.209068 -8.075108 -9.274481  ...   

                       lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-06-30 08:15:00  8.192292  7.959585  2.426879  1.094172 -1.738535   

                         lag 5     lag 4      lag 3      lag 2      lag 1  
2020-06-30 08:15:00 -10.371241 -7.137281 -12.203321 -15.602695 -15.402068  

[1 rows x 107 columns]
[-15.091757]
-17.034774689284358
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-30 08:30:00 -0.612827 -3.878867  1.021759  0.155719  3.823012   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-30 08:30:00  1.490306 -7.209068 -8.075108 -9.274481 -9.607188  ...   

    

[-18.751938]
-18.859334937732307
                       lag 107    lag 106   lag 105    lag 104    lag 103  \
2020-06-30 12:00:00 -12.470721 -11.836761 -9.636134 -11.135508 -14.168214   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 12:00:00 -13.600921 -13.466961 -16.233001 -16.232375 -16.665081   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-06-30 12:00:00  ... -18.598308 -18.764348 -18.930388 -18.663095   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-06-30 12:00:00 -19.162468 -18.728508 -18.994548 -18.893922 -18.826628   

                         lag 1  
2020-06-30 12:00:00 -18.859335  

[1 rows x 107 columns]
[-18.897684]
-18.892041622145257
                       lag 107   lag 106    lag 105    lag 104    lag 103  \
2020-06-30 12:15:00 -11.836761 -9.636134 -11.135508 -14.168214 -13.600921   

                       lag 102    lag 101    lag 100     lag 99     lag 98 

[-16.429459]
-16.98389518618026
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 15:30:00 -18.695281 -18.361321 -18.260695 -18.593401 -18.492775   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 15:30:00 -18.558815 -18.658188 -18.390895 -18.590268 -18.389641   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-06-30 15:30:00  ... -18.756202 -18.955575 -18.921615 -18.687655   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-06-30 15:30:00 -18.987028 -18.586402 -17.919108 -17.851815 -17.451189   

                         lag 1  
2020-06-30 15:30:00 -16.983895  

[1 rows x 107 columns]
[-17.061897]
-16.983268537259875
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 15:45:00 -18.361321 -18.260695 -18.593401 -18.492775 -18.558815   

                       lag 102    lag 101    lag 100     lag 99     lag 

[-11.1377535]
-10.541788767961542
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 19:00:00 -18.519842 -18.552548 -18.518588 -18.217962 -18.117335   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 19:00:00 -18.350042 -18.449415 -18.448788 -18.181495 -18.214202   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-06-30 19:00:00  ... -14.580762 -14.413469 -13.812842 -13.078882   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-06-30 19:00:00 -12.978255 -12.344295 -11.977002 -11.143042 -10.342415   

                         lag 1  
2020-06-30 19:00:00 -10.541789  

[1 rows x 107 columns]
[-11.41762]
-10.041162119041156
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 19:15:00 -18.552548 -18.518588 -18.217962 -18.117335 -18.350042   

                       lag 102    lag 101    lag 100     lag 99     lag

[-7.070396]
-0.3330156830761615
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 22:30:00 -17.577735 -18.110442 -17.876482 -16.575855 -16.608562   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 22:30:00 -16.207935 -16.673975 -16.306682 -16.472722 -17.338762   

                     ...    lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-06-30 22:30:00  ... -7.571989 -7.471362 -6.804069 -6.003442 -4.336149   

                         lag 5      lag 4     lag 3     lag 2     lag 1  
2020-06-30 22:30:00  18.397811  13.331771 -1.300936 -7.933642 -0.333016  

[1 rows x 107 columns]
[6.3860655]
-2.29905570082244
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 22:45:00 -18.110442 -17.876482 -16.575855 -16.608562 -16.207935   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 22:45:00 -16.673975 -16.306682 -16.472722 -17.338

In [13]:
mse4 = runModels(df4,df3.iloc[-107:])

                       lag 107    lag 106    lag 105    lag 104    lag 103  \
Dates                                                                        
2020-10-01 00:00:00 -24.529253 -24.297302 -24.998685 -24.466735 -24.668118   
2020-10-01 00:15:00 -24.297302 -24.998685 -24.466735 -24.668118 -24.502834   
2020-10-01 00:30:00 -24.998685 -24.466735 -24.668118 -24.502834 -24.404217   
2020-10-01 00:45:00 -24.466735 -24.668118 -24.502834 -24.404217 -24.672267   
2020-10-01 01:00:00 -24.668118 -24.502834 -24.404217 -24.672267 -24.406983   
...                        ...        ...        ...        ...        ...   
2020-12-13 13:00:00 -36.091985 -35.993458 -35.961597 -36.296402 -35.964541   
2020-12-13 13:15:00 -35.993458 -35.961597 -36.296402 -35.964541 -35.632680   
2020-12-13 13:30:00 -35.961597 -36.296402 -35.964541 -35.632680 -36.134153   
2020-12-13 13:45:00 -36.296402 -35.964541 -35.632680 -36.134153 -35.968958   
2020-12-13 14:00:00 -35.964541 -35.632680 -36.134153 -35.968958 

C:\Users\bvits\AppData\Local\Temp\ipykernel_41448\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_41448\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_41448\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider

                       lag 107    lag 106    lag 105    lag 104    lag 103  \
Dates                                                                        
2020-12-13 14:15:00 -35.632680 -36.134153 -35.968958 -36.037097 -34.271903   
2020-12-13 14:30:00 -36.134153 -35.968958 -36.037097 -34.271903 -33.973375   
2020-12-13 14:45:00 -35.968958 -36.037097 -34.271903 -33.973375 -33.774848   
2020-12-13 15:00:00 -36.037097 -34.271903 -33.973375 -33.774848 -34.642987   
2020-12-13 15:15:00 -34.271903 -33.973375 -33.774848 -34.642987 -35.544459   
...                        ...        ...        ...        ...        ...   
2020-12-31 22:45:00 -12.944065   7.221206  28.253144  28.985081  30.517019   
2020-12-31 23:00:00   7.221206  28.253144  28.985081  30.517019  40.448957   
2020-12-31 23:15:00  28.253144  28.985081  30.517019  40.448957  34.680895   
2020-12-31 23:30:00  28.985081  30.517019  40.448957  34.680895  17.846166   
2020-12-31 23:45:00  30.517019  40.448957  34.680895  17.846166 

[116.72279]
115.48020521180791
                       lag 107    lag 106    lag 105   lag 104    lag 103  \
2020-12-13 17:45:00 -25.953293 -25.654765 -23.989571 -20.95771 -20.959182   

                       lag 102   lag 101    lag 100     lag 99     lag 98  \
2020-12-13 17:45:00 -17.527321 -15.79546 -14.630266 -11.398405 -11.599877   

                     ...      lag 10       lag 9       lag 8       lag 7  \
2020-12-13 17:45:00  ...  114.260014  116.791887  118.457093  118.088967   

                          lag 6       lag 5       lag 4       lag 3  \
2020-12-13 17:45:00  119.587506  118.919379  116.351253  117.849792   

                          lag 2       lag 1  
2020-12-13 17:45:00  116.481665  115.480205  

[1 rows x 107 columns]
[117.33091]
116.1787449821455
                       lag 107    lag 106   lag 105    lag 104    lag 103  \
2020-12-13 18:00:00 -25.654765 -23.989571 -20.95771 -20.959182 -17.527321   

                      lag 102    lag 101    lag 100     lag 99

[99.52549]
92.55976199653372
                      lag 107   lag 106  lag 105   lag 104   lag 103  \
2020-12-13 21:15:00 -1.807239 -0.242045  2.42315  3.955011  5.886872   

                      lag 102    lag 101    lag 100     lag 99    lag 98  ...  \
2020-12-13 21:15:00  8.452066  10.283927  11.949121  14.080982  16.17951  ...   

                         lag 10       lag 9      lag 8      lag 7       lag 6  \
2020-12-13 21:15:00  103.206237  106.071444  105.13665  111.73519  109.800396   

                          lag 5       lag 4       lag 3       lag 2      lag 1  
2020-12-13 21:15:00  103.265603  104.730809  111.029349  103.694556  92.559762  

[1 rows x 107 columns]
[81.842514]
80.5916351002046
                      lag 107  lag 106   lag 105   lag 104   lag 103  \
2020-12-13 21:30:00 -0.242045  2.42315  3.955011  5.886872  8.452066   

                       lag 102    lag 101    lag 100    lag 99     lag 98  \
2020-12-13 21:30:00  10.283927  11.949121  14.080982  16.17951 

...

[55.267265]
20.891923633599117
                      lag 107    lag 106    lag 105   lag 104    lag 103  \
2020-12-31 05:30:00 -28.64777 -19.315833 -24.217228 -25.78529 -21.886686   

                       lag 102    lag 101    lag 100    lag 99    lag 98  ...  \
2020-12-31 05:30:00 -21.154748 -17.289477 -10.690873 -6.725602 -4.460331  ...   

                         lag 10      lag 9      lag 8      lag 7       lag 6  \
2020-12-31 05:30:00  104.304484  99.603088  98.101693  97.600297  101.398902   

                         lag 5      lag 4      lag 3      lag 2      lag 1  
2020-12-31 05:30:00  97.997506  95.162777  82.828048  51.193319  20.891924  

[1 rows x 107 columns]
[3.0095844]
21.723861390432116
                       lag 107    lag 106   lag 105    lag 104    lag 103  \
2020-12-31 05:45:00 -19.315833 -24.217228 -25.78529 -21.886686 -21.154748   

                       lag 102    lag 101   lag 100    lag 99    lag 98  ...  \
2020-12-31 05:45:00 -17.289477 -10.690873 -6.725

[12.2197485]
5.46959440959388
                     lag 107    lag 106    lag 105   lag 104    lag 103  \
2020-12-31 09:30:00  50.7299  46.161838  39.060443  31.29238  23.190985   

                       lag 102   lag 101    lag 100     lag 99   lag 98  ...  \
2020-12-31 09:30:00  25.456256  22.45486  18.453465  10.685402  2.71734  ...   

                        lag 10      lag 9      lag 8      lag 7      lag 6  \
2020-12-31 09:30:00  13.815488  11.514092  13.812697  24.877968  42.776572   

                         lag 5      lag 4      lag 3      lag 2     lag 1  
2020-12-31 09:30:00  48.375177  41.473781  40.872386  20.537657  5.469594  

[1 rows x 107 columns]
[-0.32003123]
4.134865499760229
                       lag 107    lag 106   lag 105    lag 104    lag 103  \
2020-12-31 09:45:00  46.161838  39.060443  31.29238  23.190985  25.456256   

                      lag 102    lag 101    lag 100   lag 99    lag 98  ...  \
2020-12-31 09:45:00  22.45486  18.453465  10.685402  2.7173

[-33.32042]
-32.352734814411335
                      lag 107   lag 106  lag 105   lag 104    lag 103  \
2020-12-31 13:30:00  4.274238  8.239509  7.30478  7.170051  11.568656   

                       lag 102    lag 101    lag 100    lag 99    lag 98  ...  \
2020-12-31 13:30:00  23.133927  28.965864  24.364469  9.396407 -7.104989  ...   

                        lag 10     lag 9      lag 8      lag 7      lag 6  \
2020-12-31 13:30:00 -31.440175 -32.14157 -32.276299 -32.211028 -32.645757   

                         lag 5      lag 4      lag 3      lag 2      lag 1  
2020-12-31 13:30:00 -32.013819 -32.415215 -32.383277 -32.418006 -32.352735  

[1 rows x 107 columns]
[-28.681513]
-32.48746372424499
                      lag 107  lag 106   lag 105    lag 104    lag 103  \
2020-12-31 13:45:00  8.239509  7.30478  7.170051  11.568656  23.133927   

                       lag 102    lag 101   lag 100    lag 99     lag 98  ...  \
2020-12-31 13:45:00  28.965864  24.364469  9.396407 -7.104989 -

[-32.110603]
-32.70554923758724
                       lag 107    lag 106   lag 105   lag 104    lag 103  \
2020-12-31 17:00:00 -28.911967 -18.380029 -3.348091 -15.98282 -23.650883   

                       lag 102   lag 101    lag 100     lag 99    lag 98  ...  \
2020-12-31 17:00:00 -20.885611 -23.12034 -22.455069 -24.523131 -22.55786  ...   

                        lag 10      lag 9      lag 8      lag 7      lag 6  \
2020-12-31 17:00:00 -32.459713 -32.427775 -32.029171 -32.097233 -32.598619   

                         lag 5      lag 4      lag 3     lag 2      lag 1  
2020-12-31 17:00:00 -32.466672 -32.168058 -32.702777 -32.47083 -32.705549  

[1 rows x 107 columns]
[-31.59706]
-32.54026865056057
                       lag 107   lag 106   lag 105    lag 104    lag 103  \
2020-12-31 17:15:00 -18.380029 -3.348091 -15.98282 -23.650883 -20.885611   

                      lag 102    lag 101    lag 100    lag 99     lag 98  ...  \
2020-12-31 17:15:00 -23.12034 -22.455069 -24.523131 -2

[-31.686903]
-32.6957792581338
                       lag 107    lag 106   lag 105   lag 104    lag 103  \
2020-12-31 21:15:00 -20.769025 -12.370421 -3.438483  1.393455 -11.441274   

                       lag 102    lag 101   lag 100     lag 99     lag 98  \
2020-12-31 21:15:00 -18.509336 -12.944065  7.221206  28.253144  28.985081   

                     ...     lag 10      lag 9     lag 8      lag 7  \
2020-12-31 21:15:00  ... -32.583305 -32.451357 -32.31941 -32.154129   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-12-31 21:15:00 -32.122182 -32.256902 -32.558288 -32.059674 -32.594393   

                         lag 1  
2020-12-31 21:15:00 -32.695779  

[1 rows x 107 columns]
[-32.87866]
-32.6971653377738
                       lag 107   lag 106   lag 105    lag 104    lag 103  \
2020-12-31 21:30:00 -12.370421 -3.438483  1.393455 -11.441274 -18.509336   

                       lag 102   lag 101    lag 100     lag 99     lag 98  \
2020-12-31 

In [14]:
print('season 1')

print('model 1:')
print(mse1)



season 1
model 1:
[0.01157723676093123, 5.659035571089233, 0.19360310914625772, 4.5756252254038445, 1.099673679893831, 2.4281689752747453, 0.7364037385529997, 2.404106307851683, 19.9647167539756, 2.1123678390871197, 1.6544770628087833, 0.008418149370023333, 1.0802957556443717, 1.1500555176434444, 0.4459394265889585, 14.047807250133642, 0.6015644460831223, 0.29805311376700977, 1.3397905168738855, 133.28019727398464, 2.601736952383717, 1.6986283191981397, 0.011553168312486144, 1.23430686111891, 0.7872163320556814, 0.12899472319638958, 0.4375081314829061, 5.620129650553014, 54.87478405923167, 7.415015007102649, 0.19204993874468912, 0.4888672673313146, 0.03128054692387219, 0.26193712124268953, 71.79921722656931, 0.42019114929248014, 30.243818468402413, 5.289180119308769, 61.60604085197042, 5.327605622556294, 28.48345261044171, 0.8920684705176314, 15.139031566189177, 38.41148058125578, 9.895224582136446, 0.21103244134847846, 0.27444123198141296, 13.467724710323974, 1.1959319425740833, 23.28

In [15]:
print('season 1')

print('model 1:')
print(mse2)


season 1
model 1:
[1.0716091229765348, 0.6307631070492621, 0.1650414601767346, 0.004349229662573643, 0.792752032619896, 0.9217201653946927, 1.3283087066968264, 0.2614351043711848, 0.2904242284058403, 2.9685360221665817, 0.02776533215700007, 0.3207251153878451, 0.8802548143326071, 0.12897072836809348, 0.15864445402794772, 7.904041069723013, 6.262955896727765, 8.379537262516425, 1.6484140731246315, 0.8608666482076966, 191.95773103115275, 713.8397242380814, 66.5322604580473, 16.13617610865394, 4.383304835528424, 9.333470662438328, 8.18002761110186, 34.70201114038084, 8.983400292321715, 0.48039679143679515, 0.8032800239162494, 0.20073010007014377, 0.1038556694836652, 0.16629056861464336, 0.2837321037961474, 0.2026480988843294, 0.3791855581229049, 0.034475723749114805, 6.303895098581265, 0.14793836903657653, 0.7776522062217965, 3.140346545147571, 4.852061488216388, 19.873759669864253, 10.792917331644126, 3.5189688203900276, 23.661741268447585, 8.838051998963648, 49.23928749756854, 13.938629

In [16]:
print('season 1')

print('model 1:')
print(mse3)



season 1
model 1:
[0.8080550838716365, 0.8904943407642799, 0.4110055669441216, 0.022753571405004818, 0.40165311513214513, 0.19826974561166377, 0.4678530241943666, 0.5734887109128574, 9.190802817738827, 2.5837936599351625, 0.03997303015847642, 0.06447718331333745, 0.9243397478359364, 0.0942919650284382, 0.2709937913677214, 11.785203638905145, 6.649628326803793, 1.631563389400857, 0.33429224931076074, 0.6624568255865181, 197.3039759994642, 532.5356780418509, 46.18396615364644, 3.7584939646351416, 0.00017741539995491413, 1.1159255012513674, 2.267294365421721, 17.148268681830537, 7.090805931008993, 5.04695929871533, 0.009716879809171826, 0.865495629135125, 0.06512133413616605, 0.46705282972132217, 0.7275924651918487, 0.0073264800992741096, 0.03206302279778307, 0.039672604209008706, 0.6521875413352114, 0.02875842474620979, 10.929101843054152, 3.7166927508741234, 3.29199726040338, 21.453164697420124, 13.972110410471625, 6.287595206052117, 22.477073239366835, 0.32719397970938247, 14.869805877

In [17]:
print('season 1')

print('model 1:')
print(mse4)



season 1
model 1:
[1561.6773586731133, 770.55686498159, 149.8348064510863, 46.045952904209365, 20.551836134689324, 11.44606438137686, 6.258592024512348, 14.216328093451107, 50.12725060978498, 9.540577579179793, 0.23147657099739172, 0.1987248592355769, 6.0689442967793, 1.5440258505334972, 1.3274836039032891, 1.9071406495196388, 17.377085319957814, 0.00576639966164338, 0.0013022455859916942, 180.855687068672, 25.690279435492783, 196.49780724909746, 4.6114432263818586, 4.523698998334123, 138.2310207851637, 181.66253701405924, 16.45832723034951, 48.52136393129916, 1.5646981172351466, 0.23523249457098272, 120.17406351391408, 517.3560467727675, 325.8859942089087, 259.0162838845529, 346.8080593038525, 297.4430555892046, 8.738910388355714, 26.30780066639409, 29.62791128255456, 57.62512803398469, 44.541696761243045, 139.00063959954335, 15.63865509808902, 20.28837792127379, 31.718996193130618, 10.532789292849861, 5.499488667937066, 0.6346352294698668, 334.17813789636494, 376.60134959222506, 2.88

In [18]:
d = {'Season 1':mse1,'Season 2':mse2,'Season 3':mse3,'Season 4':mse4}
df_errors_GBDT = pd.DataFrame({k:pd.Series(v) for k,v in d.items()})

df_errors_GBDT.to_csv('GBDT_errors.csv')
